In [1]:
# === 配置（改成你的路径） ===
from loguru import logger
import os, pickle
from femr.labelers import load_labeled_patients
from femr.featurizers import AgeFeaturizer, CountFeaturizer, FeaturizerList

import os, json, pickle, datetime, warnings
from dataclasses import dataclass
from typing import List, Tuple, Dict, Optional

import numpy as np
import pandas as pd
from scipy.sparse import load_npz, csr_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, average_precision_score, brier_score_loss, accuracy_score

from femr.labelers import load_labeled_patients

In [2]:
ROOT_EHRSHOT = "/root/autodl-tmp/ehrshot"

# 👇 把 LABELING_FUNCTION 设成 benchmark 下的任务文件夹名（比如 "new_pancan" 或 "guo_readmission"）
LABELING_FUNCTION = "new_pancan"

# 特征
COUNT_PKL  = os.path.join(ROOT_EHRSHOT, "features", "count_features.pkl")
CLMBR_PKL  = os.path.join(ROOT_EHRSHOT, "features", "clmbr_features.pkl")

# 标签与 shots
BENCH_DIR  = os.path.join(ROOT_EHRSHOT, "benchmark", LABELING_FUNCTION)
LABELED_PATIENTS_CSV = os.path.join(BENCH_DIR, "labeled_patients.csv")
SHOTS_JSON = os.path.join(BENCH_DIR, "all_shots_data.json")   # 本次只跑 all-shot
# 单一切分文件
SPLIT_CSV  = os.path.join(ROOT_EHRSHOT, "splits", "person_id_map.csv")
# 只跑 all-shot
K_VALUES   = [1, 8, 16, 32, 64, 128, -1]
MODELS     = ["count", "clmbr"]   # 你也可以只留一个

In [3]:
# 保持你之前的 ZoneInfo 逻辑不变
def _timestamp_str():
    tz = ZoneInfo("Asia/Jakarta") if ZoneInfo else None
    import datetime as dtmod
    return dtmod.datetime.now(tz).strftime("%Y%m%d-%H%M%S%z")


In [4]:
# ==================== 工具：加载 shots、labels、特征 ====================
def load_shots(shots_json: str, task: str, ks: List[int]) -> Dict[int, Dict[int, dict]]:
    """返回 {k: {replicate: payload}}；若 ks 包含未在文件中的 k，自动忽略并提示。"""
    with open(shots_json, "r") as f:
        blob = json.load(f)
    assert task in blob, f"{shots_json} 未包含任务 {task}"
    task_dict = blob[task]
    out: Dict[int, Dict[int, dict]] = {}
    for k in ks:
        if str(k) in task_dict:
            # 有些 JSON 序列化 k 为字符串
            out[k] = {int(rep): v for rep, v in task_dict[str(k)].items()}
        elif k in task_dict:
            out[k] = {int(rep): v for rep, v in task_dict[k].items()}
        else:
            logger.warning(f"[shots] k={k} 不在 {shots_json} 中，跳过")
    return out

def instances_from_labeled_csv(path_to_labels_dir: str, task: str) -> List[Tuple[int, str, int]]:
    """读取 labeled_patients.csv，展开为 (patient_id, time_iso, value0/1) 列表"""
    lp_csv = os.path.join(path_to_labels_dir, task, "labeled_patients.csv")
    lp = load_labeled_patients(lp_csv)
    out = []
    seen = set()
    for pid, labels in lp.items():
        for lab in labels:
            t_iso = lab.time.replace(second=0, microsecond=0).isoformat(timespec="minutes")
            key = (int(pid), t_iso)
            if key in seen:  # 去重
                continue
            seen.add(key)
            val = 1 if bool(lab.value) else 0
            out.append((int(pid), t_iso, val))
    return out

def _coerce_time_str(x: str) -> str:
    """把任意可能的时间字符串规整到分钟级 ISO（YYYY-mm-ddTHH:MM）"""
    if isinstance(x, str):
        try:
            # 已经是分钟级 iso
            dt = datetime.datetime.fromisoformat(x)
        except Exception:
            # 再试几种常见格式
            try:
                dt = pd.to_datetime(x).to_pydatetime()
            except Exception:
                raise
    else:
        # 假如是 datetime
        dt = x
    return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")

def _load_rows_csv(rows_path: str) -> pd.DataFrame:
    df = pd.read_csv(rows_path)
    # 兼容列名大小写/别名
    # 期望列：patient_id, time (iso)
    # 有的导出可能用 'label_time' 或 'timestamp'
    cols = {c.lower(): c for c in df.columns}
    pid_col = cols.get("patient_id") or cols.get("pid") or list(df.columns)[0]
    time_col = cols.get("time") or cols.get("label_time") or cols.get("timestamp") or list(df.columns)[1]
    df = df[[pid_col, time_col]].copy()
    df.columns = ["patient_id", "time"]
    df["patient_id"] = df["patient_id"].astype(int)
    df["time"] = df["time"].apply(_coerce_time_str)
    return df

def _join_rows(rows_df: pd.DataFrame, samples: List[Tuple[int, str, int]]) -> Tuple[np.ndarray, np.ndarray]:
    """返回 (row_indices, y)；跳过无法在 rows_df 中对齐的样本，并打印统计。"""
    key2row = {(int(pid), t): i for i, (pid, t) in enumerate(zip(rows_df["patient_id"].values,
                                                                 rows_df["time"].values))}
    idxs = []
    ys = []
    missed = 0
    for pid, t_iso, y in samples:
        r = key2row.get((pid, t_iso))
        if r is None:
            missed += 1
            continue
        idxs.append(r)
        ys.append(int(y))
    if missed > 0:
        logger.warning(f"[align] 样本有 {missed} 条在 rows.csv 里找不到对应行，已跳过")
    return np.array(idxs, dtype=int), np.array(ys, dtype=int)

In [5]:
# === 1) 工具函数：时间戳 & 参数快照 & 写入报告 ===
import os, json
try:
    from zoneinfo import ZoneInfo  # py>=3.9
except Exception:
    ZoneInfo = None



def _snapshot_lr_params(clf):
    """
    从 clf（可能是 Pipeline 或 LogisticRegression 实例）提取训练参数。
    """
    lr = None
    if hasattr(clf, "named_steps") and "logisticregression" in clf.named_steps:
        lr = clf.named_steps["logisticregression"]
        scaler = type(clf.named_steps.get("maxabsscaler", None)).__name__ if "maxabsscaler" in clf.named_steps else None
    else:
        lr = clf
        scaler = None
    snap = {
        "is_pipeline": hasattr(clf, "named_steps"),
        "scaler": scaler,
        "solver": getattr(lr, "solver", None),
        "penalty": getattr(lr, "penalty", None),
        "C": getattr(lr, "C", None),
        "tol": getattr(lr, "tol", None),
        "max_iter": getattr(lr, "max_iter", None),
        "class_weight": getattr(lr, "class_weight", None),
        "random_state": getattr(lr, "random_state", None),
        "n_iter_": getattr(lr, "n_iter_", None),
    }
    if hasattr(snap["n_iter_"], "tolist"):
        snap["n_iter_"] = snap["n_iter_"].tolist()
    return snap

def _save_run_txt(summary_df, all_results, extra_params=None, out_dir="runs", fname_prefix="report"):
    os.makedirs(out_dir, exist_ok=True)
    ts = _timestamp_str()
    path = os.path.join(out_dir, f"{fname_prefix}-{ts}.txt")

    # 收集唯一的训练参数快照（若结果中已塞入 param_snapshot）
    param_snaps = [r.get("param_snapshot") for r in all_results if r.get("param_snapshot") is not None]
    uniq_snaps = []
    for p in param_snaps:
        if p and p not in uniq_snaps:
            uniq_snaps.append(p)

    with open(path, "w", encoding="utf-8") as f:
        f.write(f"===== Run Report =====\n")
        f.write(f"time: {ts}\n")
        if extra_params:
            f.write("\n--- run_config ---\n")
            f.write(json.dumps(extra_params, ensure_ascii=False, indent=2, sort_keys=True))
            f.write("\n")

        f.write("\n--- training_params (unique heads) ---\n")
        if uniq_snaps:
            for i, p in enumerate(uniq_snaps):
                f.write(f"[{i}] {json.dumps(p, ensure_ascii=False, indent=2, sort_keys=True)}\n")
        else:
            f.write("(no param_snapshot found in results)\n")

        f.write("\n--- SUMMARY (DataFrame) ---\n")
        f.write(summary_df.to_string(index=False))
        f.write("\n")

        f.write("\n--- ALL RESULTS (JSON per row) ---\n")
        for r in all_results:
            f.write(json.dumps(r, ensure_ascii=False, indent=2, sort_keys=True) + "\n")
    return path

In [6]:
from sklearn.metrics import precision_recall_curve, f1_score, precision_score, recall_score

def f1_at_threshold(y_true, prob, thr: float):
    pred = (prob >= thr).astype(int)
    return {
        "precision": float(precision_score(y_true, pred, zero_division=0)),
        "recall":    float(recall_score(y_true, pred, zero_division=0)),
        "f1":        float(f1_score(y_true, pred, zero_division=0)),
        "thr":       float(thr),
    }

def find_best_f1_threshold(y_true, prob):
    # 注意：precision_recall_curve 的 thresholds 长度 = len(precision)-1
    prec, rec, thr = precision_recall_curve(y_true, prob)
    f1s = 2 * prec[:-1] * rec[:-1] / (prec[:-1] + rec[:-1] + 1e-12)
    i = int(f1s.argmax())
    return float(thr[i]), float(f1s[i])

# ---------- 用 split CSV 生成 train/val/test ----------
def _detect_col(cols_map: dict, candidates: list, required=True):
    for alias in candidates:
        c = cols_map.get(alias)
        if c is not None:
            return c
    if required:
        raise ValueError(f"缺少列: {candidates}")
    return None

def _normalize_split_name(x: str) -> str:
    v = str(x).strip().lower()
    if v in {"val", "valid", "validation", "dev", "tuning"}: return "val"
    if v in {"test", "held", "heldout", "held_out"}:          return "test"
    if v in {"train", "training"}:                            return "train"
    return v

def load_pid_split_sets(split_csv: str):
    df = pd.read_csv(split_csv)
    cols = {c.lower(): c for c in df.columns}
    pid_col   = _detect_col(cols, ["person_id", "patient_id", "pid", "subject_id", "omop_person_id"])
    split_col = _detect_col(cols, ["split", "dataset", "set", "partition"])
    df["_split_norm"] = df[split_col].apply(_normalize_split_name)
    return {
        "train": set(df.loc[df["_split_norm"]=="train", pid_col].astype(int)),
        "val":   set(df.loc[df["_split_norm"]=="val",   pid_col].astype(int)),
        "test":  set(df.loc[df["_split_norm"]=="test",  pid_col].astype(int)),
    }

def _allowed_row_indices_by_split(rows_df: pd.DataFrame, split_sets: dict):
    pid = rows_df["patient_id"].astype(int).values
    return {
        "train": np.where(np.isin(pid, list(split_sets["train"])))[0],
        "val":   np.where(np.isin(pid, list(split_sets["val"])))[0],
        "test":  np.where(np.isin(pid, list(split_sets["test"])))[0],
    }

def _join_rows_with_allowed(rows_df: pd.DataFrame, samples: List[Tuple[int, str, int]], allowed_idx: np.ndarray):
    allowed = set(int(i) for i in np.asarray(allowed_idx).tolist())
    key2row = {(int(pid), t): i for i, (pid, t) in enumerate(zip(rows_df["patient_id"].values,
                                                                 rows_df["time"].values))}
    idxs, ys = [], []
    missed = wrong_split = 0
    for pid, t_iso, y in samples:
        r = key2row.get((int(pid), t_iso))
        if r is None:
            missed += 1
            continue
        if r not in allowed:
            wrong_split += 1
            continue
        idxs.append(int(r)); ys.append(int(y))
    if missed > 0:       logger.warning(f"[align] {missed} 条样本在特征行里找不到，已跳过")
    if wrong_split > 0:  logger.warning(f"[align] {wrong_split} 条样本不在该 split，已跳过")
    return np.asarray(idxs, dtype=int), np.asarray(ys, dtype=int)

def instances_from_benchmark_csv(root_bench_dir: str) -> List[Tuple[int,str,int]]:
    lp = load_labeled_patients(os.path.join(root_bench_dir, "labeled_patients.csv"))
    out, seen = [], set()
    for pid, labels in lp.items():
        for lab in labels:
            t_iso = lab.time.replace(second=0, microsecond=0).isoformat(timespec="minutes")
            key = (int(pid), t_iso)
            if key in seen: 
                continue
            seen.add(key)
            out.append((int(pid), t_iso, 1 if bool(lab.value) else 0))
    return out

In [7]:
# ------------------ Count features loader ------------------
import pickle
from scipy.sparse import csr_matrix, issparse

def _to_minute_iso(x):
    dt = pd.to_datetime(x).to_pydatetime()
    return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")

def load_count_split(path_pkl):
    """
    读取你的 count_features.pkl，结构：(X_csr, patient_ids, label_values, label_times)
    返回: (X_csr, rows_df[patient_id,time], y[0/1])
    """
    with open(path_pkl, "rb") as f:
        X, pids, y, times = pickle.load(f)

    # 矩阵统一为 CSR
    if not issparse(X):
        X = csr_matrix(np.asarray(X))
    else:
        X = X.tocsr()

    # 行索引 DataFrame（分钟级 ISO 时间）
    rows_df = pd.DataFrame({
        "patient_id": np.asarray(pids, dtype=int),
        "time": [ _to_minute_iso(t) for t in times ],
    })

    # 标签转为 0/1 int
    y = np.asarray(y)
    if y.dtype == bool:
        y = y.astype(int)
    elif np.issubdtype(y.dtype, np.integer):
        y = y.astype(int)
    else:
        # 万一保存成了 {0,1} 的 float/string
        try:
            y = y.astype(int)
        except Exception:
            vals = pd.Series(y).map(lambda v: 1 if str(v).strip() in {"1","True","true"} else 0)
            y = vals.to_numpy(dtype=int)

    assert X.shape[0] == len(rows_df) == len(y), \
        f"行数不一致: X={X.shape[0]}, rows={len(rows_df)}, y={len(y)}"

    return X, rows_df, y

def load_count_all(path_pkl):
    return load_count_split(path_pkl)    

In [8]:
# ------------------ CLMBR features loader ------------------
import os, datetime
import pickle, numpy as np, pandas as pd
from typing import Tuple

def _first_present(d: dict, keys):
    """返回 (value, key)；如果都不存在，返回 (None, None)。"""
    for k in keys:
        if k in d and d[k] is not None:
            return d[k], k
    return None, None

def load_clmbr_split(pkl_path: str) -> Tuple[object, pd.DataFrame]:
    """
    兼容几种常见存储形式：
    - dict: {"features"/"representations"/"X"/"data_matrix": array-like or sparse,
             "patient_id"/"patient_ids"/"pids": array-like,
             "time"/"times"/"label_times"/"labeling_time": array-like,
             （可选）"label_values"/"labels"/"y": array-like}
    - (features, rows_df-like) 二元组
    """
    assert os.path.exists(pkl_path), f"缺少 CLMBR 表征: {pkl_path}"
    with open(pkl_path, "rb") as f:
        obj = pickle.load(f)

    # A) 字典形式
    if isinstance(obj, dict):
        feats, fk   = _first_present(obj, ["features", "representations", "X", "data_matrix"])
        pids, pk    = _first_present(obj, ["patient_id", "patient_ids", "pids"])
        times, tk   = _first_present(obj, ["time", "times", "label_times", "labeling_time"])
        labels, lk  = _first_present(obj, ["label_values", "labels", "y"])

        if feats is None or pids is None or times is None:
            raise ValueError(
                f"{pkl_path} 里没有期望的键；已找到键：{list(obj.keys())}\n"
                f"需要 features/representations/X/data_matrix + patient_id/patient_ids/pids + time/times/label_times/labeling_time"
            )

        # 规整成 DataFrame（时间统一到分钟级 ISO）
        def _to_iso_minute(x):
            if isinstance(x, str):
                try:
                    dt = datetime.datetime.fromisoformat(x)
                except Exception:
                    dt = pd.to_datetime(x).to_pydatetime()
            else:
                dt = pd.to_datetime(x).to_pydatetime()
            return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")

        rows_df = pd.DataFrame({
            "patient_id": np.asarray(pids).astype(int),
            "time": [ _to_iso_minute(t) for t in times ],
        })
        if labels is not None and len(labels) == len(rows_df):
            rows_df["label"] = np.asarray(labels)
        # 不强制转稠密，保持原格式（ndarray 或 scipy.sparse）
        return feats, rows_df

    # B) 二元组形式: (features, rows) 或 (features, (pids, times))
    if isinstance(obj, (list, tuple)) and len(obj) == 2:
        feats, rows = obj
        if isinstance(rows, pd.DataFrame):
            rows_df = rows.copy()
        else:
            rows = np.asarray(rows)
            assert rows.shape[1] == 2, f"第二元应是两列 (patient_id, time)，实际: {rows.shape}"
            rows_df = pd.DataFrame(rows, columns=["patient_id", "time"])
        rows_df["patient_id"] = rows_df["patient_id"].astype(int)
        def _coerce(x):
            if isinstance(x, str):
                try:
                    dt = datetime.datetime.fromisoformat(x)
                except Exception:
                    dt = pd.to_datetime(x).to_pydatetime()
            else:
                dt = pd.to_datetime(x).to_pydatetime()
            return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")
        rows_df["time"] = rows_df["time"].apply(_coerce)
        return feats, rows_df

    raise ValueError(f"无法识别的 CLMBR pkl 结构：{type(obj)}（路径：{pkl_path}）")

def load_clmbr_all(path_pkl):
    return load_clmbr_split(path_pkl)          # 复用你原来的 loader

In [9]:
# ====== 逻辑回归求解器选择 ======
LR_SOLVER = "saga"     # 可选: "saga" | "lbfgs" | "auto"
LR_C_GRID = [0.3, 1.0, 3.0]
LR_BALANCED = True     # 是否用 class_weight="balanced"

from scipy.sparse import issparse
from scipy.sparse import csr_matrix, issparse
from sklearn.utils.sparsefuncs import inplace_column_scale

def _maybe_dense(X, need_dense: bool):
    """若需要致密矩阵而当前是稀疏，则转 dense。"""
    if need_dense and issparse(X):
        return X.toarray()
    return X

def _norm_triplets(pids, times, vals):
    # 统一到 (int pid, 分钟级 ISO 时间, int label)
    return [(int(p), _coerce_time_str(t), int(v)) for p, t, v in zip(pids, times, vals)]

def _ensure_csr32(X):
    if not issparse(X):
        X = csr_matrix(X)
    X = X.tocsr()
    if X.dtype != np.float32:
        X = X.astype(np.float32)
    return X

In [10]:
# ==================== 训练 & 评估 ====================
@dataclass
class SplitData:
    X:     object                 # csr_matrix 或 ndarray
    rows:  pd.DataFrame
    idxs:  np.ndarray             # 选出来的行索引
    y:     np.ndarray             # 标签(0/1)

def slice_rows(X, idxs: np.ndarray):
    if isinstance(X, csr_matrix):
        return X[idxs]
    X = np.asarray(X)
    return X[idxs]

def evaluate_binary(y_true: np.ndarray, prob: np.ndarray, thr: float = 0.5) -> Dict[str, float]:
    out = {}
    try:
        out["auroc"] = float(roc_auc_score(y_true, prob))
    except Exception:
        out["auroc"] = float("nan")
    try:
        out["auprc"] = float(average_precision_score(y_true, prob))
    except Exception:
        out["auprc"] = float("nan")
    try:
        out["brier"] = float(brier_score_loss(y_true, prob))
    except Exception:
        out["brier"] = float("nan")
    pred = (prob >= thr).astype(int)
    out["acc@0.5"] = float(accuracy_score(y_true, pred))
    out["pos_rate"] = float(np.mean(y_true))
    return out

def fit_lr_lbfgs(X_train, y_train) -> LogisticRegression:
    # 简单稳健的逻辑回归；可以按需加 class_weight="balanced"
    model = LogisticRegression(
        solver="lbfgs",
        max_iter=2000,
        n_jobs=-1,
        verbose=0,
        class_weight=None,
    )
    model.fit(X_train, y_train)
    return model

from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import MaxAbsScaler
from sklearn.linear_model import LogisticRegression
import numpy as np

def fit_lr_saga(X, y, C=1.0, tol=1e-6, max_iter=5000, balanced=False, seed=0):
    # 稀疏安全缩放 + SAGA
    class_w = "balanced" if balanced else None
    clf = make_pipeline(
        MaxAbsScaler(),
        LogisticRegression(
            solver="saga", penalty="l2", C=C, tol=tol, max_iter=max_iter,
            n_jobs=-1, verbose=0, class_weight=class_w, random_state=seed
        )
    )
    clf.fit(X, y)
    return clf

In [11]:
# ---------- 训练流程：用 split CSV 切分 ----------
def run_one_model_ehrshot(model_type: str, shots_for_k: dict, solver: str = None):
    """
    solver: "saga" | "lbfgs" | "auto"（None 时用全局 LR_SOLVER）
    - 稀疏特征（count）建议用 SAGA
    - 致密特征（clmbr）可用 LBFGS
    """
    solver = solver or LR_SOLVER
    logger.info(f"=== [{model_type}] 加载特征（EHRSHOT 模式, solver={solver}) ===")
    split_sets = load_pid_split_sets(SPLIT_CSV)

    # ---- 载全量特征，并按 train split 做一次缩放（count）；clmbr 原样 ----
    if model_type == "count":
        X_all, rows_all, _ = load_count_all(COUNT_PKL)
        train_idx_all = _allowed_row_indices_by_split(rows_all, split_sets)["train"]
        X_all = _ensure_csr32(X_all)
        scaler = MaxAbsScaler(copy=False)
        scaler.fit(X_all[train_idx_all])
        scale = scaler.scale_.astype(np.float32)
        inv = np.ones_like(scale, dtype=np.float32); inv[scale != 0] = 1.0 / scale[scale != 0]
        X_scaled = X_all.copy(); inplace_column_scale(X_scaled, inv)
    else:
        X_all, rows_all = load_clmbr_all(CLMBR_PKL)

    split_row_idxs = _allowed_row_indices_by_split(rows_all, split_sets)

    # ---- 测试集：labeled_patients.csv ∩ test 病人 ----
    held_instances = instances_from_benchmark_csv(BENCH_DIR)
    idx_te_all, y_te_all = _join_rows(rows_all, held_instances)
    test_allowed = set(split_row_idxs["test"].tolist())
    keep_mask = [i for i in idx_te_all if i in test_allowed]
    idx_te = np.array(keep_mask, dtype=int)
    y_te   = y_te_all[np.isin(idx_te_all, keep_mask)]
    logger.info(f"[{model_type}] test 对齐: {len(idx_te)}/{len(held_instances)}")

    # ---- 根据 solver 与特征稀疏性决定是否需要 dense ----
    # auto: 稀疏->saga, 致密->lbfgs
    if solver == "auto":
        need_dense = False
        if model_type == "count":
            solver_eff = "saga"
        else:
            solver_eff = "lbfgs"
    else:
        solver_eff = solver
        # lbfgs 不支持稀疏输入；若是 count（稀疏）+ lbfgs，则需要转 dense（可能占内存）
        need_dense = (solver_eff == "lbfgs" and model_type == "count")

    results = []
    for rep, payload in shots_for_k.items():
        tr_samples = _norm_triplets(
            payload["patient_ids_train_k"],
            payload["label_times_train_k"],
            payload["label_values_train_k"],
        )
        va_samples = _norm_triplets(
            payload["patient_ids_val_k"],
            payload["label_times_val_k"],
            payload["label_values_val_k"],
        )
        idx_tr, y_tr = _join_rows_with_allowed(rows_all, tr_samples, split_row_idxs["train"])
        idx_va, y_va = _join_rows_with_allowed(rows_all, va_samples, split_row_idxs["val"])
        logger.info(f"[{model_type}|rep={rep}] train 对齐: {len(idx_tr)}/{len(tr_samples)}, val 对齐: {len(idx_va)}/{len(va_samples)}")
 

        # 切片 + （如需）致密化
        if model_type == "count":
            Xtr_raw = slice_rows(X_scaled, idx_tr)
            Xva_raw = slice_rows(X_scaled, idx_va)
            Xte_raw = slice_rows(X_scaled, idx_te)
        else:
            Xtr_raw = slice_rows(X_all, idx_tr)
            Xva_raw = slice_rows(X_all, idx_va)
            Xte_raw = slice_rows(X_all, idx_te)

        Xtr = _maybe_dense(Xtr_raw, need_dense)
        Xva = _maybe_dense(Xva_raw, need_dense)
        Xte = _maybe_dense(Xte_raw, need_dense)

        # ===== 训练（两种求解器共用同一 C 网格） =====
        best = None
        for C in LR_C_GRID:
            if solver_eff == "saga":
                clf_try = fit_lr_saga_staged(
                    Xtr, y_tr, C=C, seed=rep, max_total=2000, step=200,
                    tol=1e-4, balanced=LR_BALANCED, verbose=1
                )
            elif solver_eff == "lbfgs":
                class_w = "balanced" if LR_BALANCED else None
                clf_try = LogisticRegression(
                    solver="lbfgs", penalty="l2", C=C, tol=1e-6, max_iter=2000,
                    n_jobs=-1, verbose=0, class_weight=class_w, random_state=rep
                )
                clf_try.fit(Xtr, y_tr)
            else:
                raise ValueError("solver must be 'saga', 'lbfgs', or 'auto'")

            p_va_try = clf_try.predict_proba(Xva)[:, 1]
            auroc = roc_auc_score(y_va, p_va_try)
            if best is None or auroc > best[0]:
                best = (auroc, C, clf_try)

        logger.info(f"[{model_type}|rep={rep}] {solver_eff.upper()} best C={best[1]} (AUROC={best[0]:.4f})")
        clf = best[2]

        # ===== 评估 =====
        p_tr = clf.predict_proba(Xtr)[:, 1]
        p_va = clf.predict_proba(Xva)[:, 1]
        p_te = clf.predict_proba(Xte)[:, 1]

        m_tr = evaluate_binary(y_tr, p_tr)
        m_va = evaluate_binary(y_va, p_va)
        m_te = evaluate_binary(y_te, p_te)

        best_thr, _ = find_best_f1_threshold(y_va, p_va)
        f1_05_tr = f1_at_threshold(y_tr, p_tr, 0.5)
        f1_05_va = f1_at_threshold(y_va, p_va, 0.5)
        f1_05_te = f1_at_threshold(y_te, p_te, 0.5)
        f1b_tr = f1_at_threshold(y_tr, p_tr, best_thr)
        f1b_va = f1_at_threshold(y_va, p_va, best_thr)
        f1b_te = f1_at_threshold(y_te, p_te, best_thr)

        param_snapshot = _snapshot_lr_params(clf)
        results.append({
            "model": model_type, "rep": int(rep),
            "metrics_train": m_tr, "metrics_val": m_va, "metrics_test": m_te,
            "thresholds": {"fixed_0.5": 0.5, "best_on_val": best_thr},
            "f1_at_0.5": {"train": {"f1": f1_05_tr["f1"], "precision": f1_05_tr["precision"], "recall": f1_05_tr["recall"]},
                          "val":   {"f1": f1_05_va["f1"], "precision": f1_05_va["precision"], "recall": f1_05_va["recall"]},
                          "test":  {"f1": f1_05_te["f1"], "precision": f1_05_te["precision"], "recall": f1_05_te["recall"]}},
            "f1_at_best": {"train": {"f1": f1b_tr["f1"], "precision": f1b_tr["precision"], "recall": f1b_tr["recall"]},
                           "val":   {"f1": f1b_va["f1"], "precision": f1b_va["precision"], "recall": f1b_va["recall"]},
                           "test":  {"f1": f1b_te["f1"], "precision": f1b_te["precision"], "recall": f1b_te["recall"]}},
            "param_snapshot": param_snapshot,
            "data_stats": {"n_train": int(len(y_tr)), "pos_train": int(y_tr.sum()),
                           "n_val": int(len(y_va)),   "pos_val":  int(y_va.sum()),
                           "n_test": int(len(y_te)),  "pos_test": int(y_te.sum())},
        })
    return results

def eval_one_model_ehrshot(model_name: str, save_txt: bool = True, out_dir: str = "runs"):
    assert os.path.exists(SHOTS_JSON), f"找不到 shots JSON: {SHOTS_JSON}"
    shots = load_shots(SHOTS_JSON, LABELING_FUNCTION, K_VALUES)

    all_results = []
    for k, reps in shots.items():
        logger.info(f"******** K={k}（{'ALL' if k==-1 else 'FEW'}） | model={model_name} ********")
        res = run_one_model_ehrshot(model_name, reps)
        for r in res:
            r["k"] = k; r["model"] = model_name
        all_results.extend(res)

    rows = []
    for r in all_results:
        rows.append({
            "k": r["k"], "model": r["model"], "rep": r["rep"],
            "val_auroc": r["metrics_val"]["auroc"], "val_auprc": r["metrics_val"]["auprc"], "val_brier": r["metrics_val"]["brier"],
            "test_auroc": r["metrics_test"]["auroc"], "test_auprc": r["metrics_test"]["auprc"], "test_brier": r["metrics_test"]["brier"],
            "test_acc@0.5": r["metrics_test"]["acc@0.5"], "test_pos_rate": r["metrics_test"]["pos_rate"],
            "val_f1@0.5": r["f1_at_0.5"]["val"]["f1"], "test_f1@0.5": r["f1_at_0.5"]["test"]["f1"],
            "val_f1@best": r["f1_at_best"]["val"]["f1"], "test_f1@best": r["f1_at_best"]["test"]["f1"],
            "best_thr": r["thresholds"]["best_on_val"],
        })
    summary = pd.DataFrame(rows).sort_values(by=["k","model","rep"]).reset_index(drop=True)
    print(f"\n===== Summary for model: {model_name} =====")
    print(summary)

    if save_txt:
        out_dir = os.path.join(out_dir, LABELING_FUNCTION)
        extra = {"model": model_name, "k_values": list(shots.keys()), "dataset": "ehrshot"}
        out_fp = _save_run_txt(summary, all_results, extra_params=extra, out_dir=out_dir, fname_prefix=f"{model_name}")
        print(f"[Saved] TXT report -> {out_fp}")

    return summary, all_results

In [14]:
for m in MODELS:
    eval_one_model_ehrshot(m, save_txt=True, out_dir="runs_ehrshot")

2025-09-16 04:00:24.960 | INFO     | __main__:eval_one_model_ehrshot:147 - ******** K=1（FEW） | model=count ********
2025-09-16 04:00:24.961 | INFO     | __main__:run_one_model_ehrshot:9 - === [count] 加载特征（EHRSHOT 模式, solver=saga) ===
2025-09-16 04:01:01.520 | INFO     | __main__:run_one_model_ehrshot:34 - [count] test 对齐: 2220/7011
2025-09-16 04:01:01.959 | INFO     | __main__:run_one_model_ehrshot:63 - [count|rep=0] train 对齐: 2/2, val 对齐: 2/2
/root/miniconda3/envs/ehr-env/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s finished


Epoch 1, change: 1.00000000
Epoch 2, change: 0.48781052
Epoch 3, change: 0.32833004
Epoch 4, change: 0.23090911
Epoch 5, change: 0.18434466
Epoch 6, change: 0.15193591
Epoch 7, change: 0.13144714
Epoch 8, change: 0.11513539
Epoch 9, change: 0.09130763
Epoch 10, change: 0.08240929
Epoch 11, change: 0.07453141
Epoch 12, change: 0.06672660
Epoch 13, change: 0.06052310
Epoch 14, change: 0.05551987
Epoch 15, change: 0.05209800
Epoch 16, change: 0.04641452
Epoch 17, change: 0.04269988
Epoch 18, change: 0.04105660
Epoch 19, change: 0.03721197
Epoch 20, change: 0.03553116
Epoch 21, change: 0.03397637
Epoch 22, change: 0.02937874
Epoch 23, change: 0.02917964
Epoch 24, change: 0.02633882
Epoch 25, change: 0.02530060
Epoch 26, change: 0.02443396
Epoch 27, change: 0.02243544
Epoch 28, change: 0.02138714
Epoch 29, change: 0.02040668
Epoch 30, change: 0.01925962
Epoch 31, change: 0.01870957
Epoch 32, change: 0.01731214
Epoch 33, change: 0.01659600
Epoch 34, change: 0.01633854
Epoch 35, change: 0.014

/root/miniconda3/envs/ehr-env/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s finished


2062
Epoch 5, change: 0.00071485
Epoch 6, change: 0.00070758
Epoch 7, change: 0.00070642
Epoch 8, change: 0.00070374
Epoch 9, change: 0.00067361
Epoch 10, change: 0.00066859
Epoch 11, change: 0.00066325
Epoch 12, change: 0.00065356
Epoch 13, change: 0.00064575
Epoch 14, change: 0.00063914
Epoch 15, change: 0.00063678
Epoch 16, change: 0.00062206
Epoch 17, change: 0.00061333
Epoch 18, change: 0.00061371
Epoch 19, change: 0.00060110
Epoch 20, change: 0.00059879
Epoch 21, change: 0.00059649
Epoch 22, change: 0.00057300
Epoch 23, change: 0.00057721
Epoch 24, change: 0.00056177
Epoch 25, change: 0.00055865
Epoch 26, change: 0.00055661
Epoch 27, change: 0.00054390
Epoch 28, change: 0.00053855
Epoch 29, change: 0.00053330
Epoch 30, change: 0.00052581
Epoch 31, change: 0.00052392
Epoch 32, change: 0.00051204
Epoch 33, change: 0.00050705
Epoch 34, change: 0.00050733
Epoch 35, change: 0.00049280
Epoch 36, change: 0.00048923
Epoch 37, change: 0.00048331
Epoch 38, change: 0.00047761
Epoch 39, chan

/root/miniconda3/envs/ehr-env/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.1s finished
/root/miniconda3/envs/ehr-env/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.2s finished
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:    0.0s finished
2025-09-16 04:01:02.697 | INFO     | __main__:run_one_model_ehrshot:103 - [count|rep=0] SAGA best C=0.3 (AUROC=1.0000)


...

82, change: 0.00103775
Epoch 183, change: 0.00103515
Epoch 184, change: 0.00101051
Epoch 185, change: 0.00102571
Epoch 186, change: 0.00096450
Epoch 187, change: 0.00100280
Epoch 188, change: 0.00099892
Epoch 189, change: 0.00095671
Epoch 190, change: 0.00094953
Epoch 191, change: 0.00094686
Epoch 192, change: 0.00095593
Epoch 193, change: 0.00089802
Epoch 194, change: 0.00090344
Epoch 195, change: 0.00089988
Epoch 196, change: 0.00090440
Epoch 197, change: 0.00087487
Epoch 198, change: 0.00088616
Epoch 199, change: 0.00087355
Epoch 200, change: 0.00086437
Epoch 1, change: 1.00000000
Epoch 2, change: 0.00362029
Epoch 3, change: 0.00237355
Epoch 4, change: 0.00147330
Epoch 5, change: 0.00111326
Epoch 6, change: 0.00089033
Epoch 7, change: 0.00076906
Epoch 8, change: 0.00081008
Epoch 9, change: 0.00067841
Epoch 10, change: 0.00072263
Epoch 11, change: 0.00081921
Epoch 12, change: 0.00081112
Epoch 13, change: 0.00073953
Epoch 14, change: 0.00078618
Epoch 15, change: 0.00074912
Epoch 16, c

/root/miniconda3/envs/ehr-env/lib/python3.10/site-packages/sklearn/linear_model/_sag.py:350: ConvergenceWarning: The max_iter was reached which means the coef_ did not converge
  warnings.warn(
[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   14.6s finished


ange: 0.00018976
Epoch 396, change: 0.00018872
Epoch 397, change: 0.00018816
Epoch 398, change: 0.00018752
Epoch 399, change: 0.00018812
Epoch 400, change: 0.00018841
Epoch 1, change: 1.00000000
Epoch 2, change: 0.00194546
Epoch 3, change: 0.00129766
Epoch 4, change: 0.00068636
Epoch 5, change: 0.00061673
Epoch 6, change: 0.00036492
Epoch 7, change: 0.00032962
Epoch 8, change: 0.00024628
Epoch 9, change: 0.00024143
Epoch 10, change: 0.00023122
Epoch 11, change: 0.00021069
Epoch 12, change: 0.00024121
Epoch 13, change: 0.00019506
Epoch 14, change: 0.00020131
Epoch 15, change: 0.00019838
Epoch 16, change: 0.00019379
Epoch 17, change: 0.00018578
Epoch 18, change: 0.00018866
Epoch 19, change: 0.00018883
Epoch 20, change: 0.00018641
Epoch 21, change: 0.00018218
Epoch 22, change: 0.00017973
Epoch 23, change: 0.00018022
Epoch 24, change: 0.00017964
Epoch 25, change: 0.00017826
Epoch 26, change: 0.00017644
Epoch 27, change: 0.00017442
Epoch 28, change: 0.00017580
Epoch 29, change: 0.00017518
E

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   13.9s finished
2025-09-16 04:14:11.774 | INFO     | __main__:run_one_model_ehrshot:103 - [clmbr|rep=0] SAGA best C=0.3 (AUROC=0.7869)


convergence after 379 epochs took 14 seconds

===== Summary for model: clmbr =====
      k  model  rep  val_auroc  val_auprc  val_brier  test_auroc  test_auprc  \
0    -1  clmbr    0   0.786894   0.101022   0.068045    0.706405    0.103243   
1     1  clmbr    0   0.000000   0.500000   0.328383    0.575010    0.038436   
2     1  clmbr    1   0.000000   0.500000   0.344086    0.654187    0.111418   
3     1  clmbr    2   0.000000   0.500000   0.382176    0.619265    0.042259   
4     1  clmbr    3   1.000000   1.000000   0.216772    0.597653    0.043361   
5     1  clmbr    4   1.000000   1.000000   0.184226    0.599460    0.051360   
6     8  clmbr    0   0.937500   0.941518   0.097964    0.713180    0.063350   
7     8  clmbr    1   0.609375   0.601668   0.343979    0.712932    0.089883   
8     8  clmbr    2   0.671875   0.705952   0.267724    0.594682    0.040995   
9     8  clmbr    3   0.734375   0.816117   0.193927    0.686064    0.110360   
10    8  clmbr    4   0.890625   0.86

In [29]:
df = pd.read_csv(SPLIT_CSV)

In [30]:
print(df)

      split  omop_person_id
0       val       115971637
1       val       115970526
2       val       115968232
3       val       115969919
4       val       115968793
...     ...             ...
6734  train       115973721
6735  train       115972195
6736  train       115967959
6737  train       115972479
6738  train       115971507

[6739 rows x 2 columns]


In [2]:
BASE = "/root/autodl-tmp/femr"
SPLITS = {
    "train":    {"db": f"{BASE}/train/extract",    "labels": f"{BASE}/train/femr_labels", "features": f"{BASE}/train/femr_features"},
    "tuning":   {"db": f"{BASE}/tuning/extract",   "labels": f"{BASE}/tuning/femr_labels", "features": f"{BASE}/tuning/femr_features"},
    "held_out": {"db": f"{BASE}/held_out/extract", "labels": f"{BASE}/held_out/femr_labels", "features": f"{BASE}/held_out/femr_features"},
}

NUM_THREADS = 15  # notebook 里先小一点；命令行可开大
FORCE = True

In [7]:
import os, json, pickle, datetime, warnings
from dataclasses import dataclass
from typing import List, Tuple, Dict, Optional

import numpy as np
import pandas as pd
from scipy.sparse import load_npz, csr_matrix
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import roc_auc_score, average_precision_score, brier_score_loss, accuracy_score
from loguru import logger

from femr.labelers import load_labeled_patients

In [20]:
ROOT = "/root/autodl-tmp/femr"
LABELING_FUNCTION = "mimic_icu_mortality"

# 三个 split 的目录
TRAIN = {
    "db":       f"{ROOT}/train/extract",
    "labels":   f"{ROOT}/train/femr_labels",
    "features": f"{ROOT}/train/femr_features",
}
TUNING = {
    "db":       f"{ROOT}/tuning/extract",
    "labels":   f"{ROOT}/tuning/femr_labels",
    "features": f"{ROOT}/tuning/femr_features",
}
HELDOUT = {
    "db":       f"{ROOT}/held_out/extract",
    "labels":   f"{ROOT}/held_out/femr_labels",
    "features": f"{ROOT}/held_out/femr_features",
}

In [21]:
# #6 生成的 shots JSON（放在 train 任务目录下）
SHOT_STRAT = "all"  # 或 "few"
SHOTS_JSON = os.path.join(TRAIN["labels"], LABELING_FUNCTION, f"{SHOT_STRAT}_shots_data.json")
K_VALUES   = [-1]   # all 模式：[-1]；few 模式举例：[8,16,32]
# 选择要训练的表征：["count"]、["clmbr"]、或 ["count","clmbr"]
MODELS = ["count", "clmbr"]

In [22]:
# ============ 如果你的文件名跟下述不同，改这部分的显式路径 =============
# Count features（常见存放）
COUNT_FILES = {
    "train": os.path.join(TRAIN["features"], "count_features.pkl"),
    "tuning": os.path.join(TUNING["features"], "count_features.pkl"),
    "held":   os.path.join(HELDOUT["features"], "count_features.pkl"),
}

# CLMBR features（常见存放）
CLMBR_FILES = {
    "train": os.path.join(TRAIN["features"], "clmbr_features.pkl"),
    "tuning":os.path.join(TUNING["features"], "clmbr_features.pkl"),
    "held":  os.path.join(HELDOUT["features"], "clmbr_features.pkl"),
}
# =================================================================

In [8]:
# ------------------ Count features loader ------------------
import pickle
from scipy.sparse import csr_matrix, issparse

def _to_minute_iso(x):
    dt = pd.to_datetime(x).to_pydatetime()
    return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")

def load_count_split(path_pkl):
    """
    读取你的 count_features.pkl，结构：(X_csr, patient_ids, label_values, label_times)
    返回: (X_csr, rows_df[patient_id,time], y[0/1])
    """
    with open(path_pkl, "rb") as f:
        X, pids, y, times = pickle.load(f)

    # 矩阵统一为 CSR
    if not issparse(X):
        X = csr_matrix(np.asarray(X))
    else:
        X = X.tocsr()

    # 行索引 DataFrame（分钟级 ISO 时间）
    rows_df = pd.DataFrame({
        "patient_id": np.asarray(pids, dtype=int),
        "time": [ _to_minute_iso(t) for t in times ],
    })

    # 标签转为 0/1 int
    y = np.asarray(y)
    if y.dtype == bool:
        y = y.astype(int)
    elif np.issubdtype(y.dtype, np.integer):
        y = y.astype(int)
    else:
        # 万一保存成了 {0,1} 的 float/string
        try:
            y = y.astype(int)
        except Exception:
            vals = pd.Series(y).map(lambda v: 1 if str(v).strip() in {"1","True","true"} else 0)
            y = vals.to_numpy(dtype=int)

    assert X.shape[0] == len(rows_df) == len(y), \
        f"行数不一致: X={X.shape[0]}, rows={len(rows_df)}, y={len(y)}"

    return X, rows_df, y


In [24]:
COUNT_FILES = {
    "train": "/root/autodl-tmp/femr/train/femr_features/count_features.pkl",
    "tuning":"/root/autodl-tmp/femr/tuning/femr_features/count_features.pkl",
    "held":  "/root/autodl-tmp/femr/held_out/femr_features/count_features.pkl",
}

for split, p in COUNT_FILES.items():
    X, rows, y = load_count_split(p)
    pos = int(y.sum()); n = len(y)
    print(f"{split:7s} | X={X.shape}, rows={rows.shape}, pos={pos}/{n} ({pos/n:.3%})")
    print(rows.head(2), "\n")


train   | X=(46113, 51281), rows=(46113, 2), pos=0/46113 (0.000%)
   patient_id              time
0    10001217  2157-11-21T19:18
1    10001725  2110-04-12T15:52 

tuning  | X=(5602, 51281), rows=(5602, 2), pos=0/5602 (0.000%)
   patient_id              time
0    10002155  2129-08-05T12:45
1    10002155  2130-09-25T00:50 

held    | X=(5815, 51281), rows=(5815, 2), pos=0/5815 (0.000%)
   patient_id              time
0    10002428  2156-04-13T16:24
1    10002428  2156-04-20T18:11 



In [25]:
# 样本级对齐抽查：随机看 3 条
import numpy as np
rng = np.random.default_rng(0)
X, rows, y = load_count_split(COUNT_FILES["train"])
idxs = rng.choice(len(rows), size=3, replace=False)
print(rows.iloc[idxs].assign(y=y[idxs]).to_string(index=False))


 patient_id             time  y
   16346901 2175-01-06T10:15  0
   15106570 2122-01-09T16:45  0
   18506917 2177-03-31T21:58  0


In [9]:
from sklearn.metrics import precision_recall_curve, f1_score, precision_score, recall_score

def f1_at_threshold(y_true, prob, thr: float):
    pred = (prob >= thr).astype(int)
    return {
        "precision": float(precision_score(y_true, pred, zero_division=0)),
        "recall":    float(recall_score(y_true, pred, zero_division=0)),
        "f1":        float(f1_score(y_true, pred, zero_division=0)),
        "thr":       float(thr),
    }

def find_best_f1_threshold(y_true, prob):
    # 注意：precision_recall_curve 的 thresholds 长度 = len(precision)-1
    prec, rec, thr = precision_recall_curve(y_true, prob)
    f1s = 2 * prec[:-1] * rec[:-1] / (prec[:-1] + rec[:-1] + 1e-12)
    i = int(f1s.argmax())
    return float(thr[i]), float(f1s[i])

In [10]:
# ==================== 工具：加载 shots、labels、特征 ====================
def load_shots(shots_json: str, task: str, ks: List[int]) -> Dict[int, Dict[int, dict]]:
    """返回 {k: {replicate: payload}}；若 ks 包含未在文件中的 k，自动忽略并提示。"""
    with open(shots_json, "r") as f:
        blob = json.load(f)
    assert task in blob, f"{shots_json} 未包含任务 {task}"
    task_dict = blob[task]
    out: Dict[int, Dict[int, dict]] = {}
    for k in ks:
        if str(k) in task_dict:
            # 有些 JSON 序列化 k 为字符串
            out[k] = {int(rep): v for rep, v in task_dict[str(k)].items()}
        elif k in task_dict:
            out[k] = {int(rep): v for rep, v in task_dict[k].items()}
        else:
            logger.warning(f"[shots] k={k} 不在 {shots_json} 中，跳过")
    return out

def instances_from_labeled_csv(path_to_labels_dir: str, task: str) -> List[Tuple[int, str, int]]:
    """读取 labeled_patients.csv，展开为 (patient_id, time_iso, value0/1) 列表"""
    lp_csv = os.path.join(path_to_labels_dir, task, "labeled_patients.csv")
    lp = load_labeled_patients(lp_csv)
    out = []
    seen = set()
    for pid, labels in lp.items():
        for lab in labels:
            t_iso = lab.time.replace(second=0, microsecond=0).isoformat(timespec="minutes")
            key = (int(pid), t_iso)
            if key in seen:  # 去重
                continue
            seen.add(key)
            val = 1 if bool(lab.value) else 0
            out.append((int(pid), t_iso, val))
    return out

def _coerce_time_str(x: str) -> str:
    """把任意可能的时间字符串规整到分钟级 ISO（YYYY-mm-ddTHH:MM）"""
    if isinstance(x, str):
        try:
            # 已经是分钟级 iso
            dt = datetime.datetime.fromisoformat(x)
        except Exception:
            # 再试几种常见格式
            try:
                dt = pd.to_datetime(x).to_pydatetime()
            except Exception:
                raise
    else:
        # 假如是 datetime
        dt = x
    return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")

def _load_rows_csv(rows_path: str) -> pd.DataFrame:
    df = pd.read_csv(rows_path)
    # 兼容列名大小写/别名
    # 期望列：patient_id, time (iso)
    # 有的导出可能用 'label_time' 或 'timestamp'
    cols = {c.lower(): c for c in df.columns}
    pid_col = cols.get("patient_id") or cols.get("pid") or list(df.columns)[0]
    time_col = cols.get("time") or cols.get("label_time") or cols.get("timestamp") or list(df.columns)[1]
    df = df[[pid_col, time_col]].copy()
    df.columns = ["patient_id", "time"]
    df["patient_id"] = df["patient_id"].astype(int)
    df["time"] = df["time"].apply(_coerce_time_str)
    return df

def _join_rows(rows_df: pd.DataFrame, samples: List[Tuple[int, str, int]]) -> Tuple[np.ndarray, np.ndarray]:
    """返回 (row_indices, y)；跳过无法在 rows_df 中对齐的样本，并打印统计。"""
    key2row = {(int(pid), t): i for i, (pid, t) in enumerate(zip(rows_df["patient_id"].values,
                                                                 rows_df["time"].values))}
    idxs = []
    ys = []
    missed = 0
    for pid, t_iso, y in samples:
        r = key2row.get((pid, t_iso))
        if r is None:
            missed += 1
            continue
        idxs.append(r)
        ys.append(int(y))
    if missed > 0:
        logger.warning(f"[align] 样本有 {missed} 条在 rows.csv 里找不到对应行，已跳过")
    return np.array(idxs, dtype=int), np.array(ys, dtype=int)

In [11]:
# ------------------ CLMBR features loader ------------------
import os, datetime
import pickle, numpy as np, pandas as pd
from typing import Tuple

def _first_present(d: dict, keys):
    """返回 (value, key)；如果都不存在，返回 (None, None)。"""
    for k in keys:
        if k in d and d[k] is not None:
            return d[k], k
    return None, None

def load_clmbr_split(pkl_path: str) -> Tuple[object, pd.DataFrame]:
    """
    兼容几种常见存储形式：
    - dict: {"features"/"representations"/"X"/"data_matrix": array-like or sparse,
             "patient_id"/"patient_ids"/"pids": array-like,
             "time"/"times"/"label_times"/"labeling_time": array-like,
             （可选）"label_values"/"labels"/"y": array-like}
    - (features, rows_df-like) 二元组
    """
    assert os.path.exists(pkl_path), f"缺少 CLMBR 表征: {pkl_path}"
    with open(pkl_path, "rb") as f:
        obj = pickle.load(f)

    # A) 字典形式
    if isinstance(obj, dict):
        feats, fk   = _first_present(obj, ["features", "representations", "X", "data_matrix"])
        pids, pk    = _first_present(obj, ["patient_id", "patient_ids", "pids"])
        times, tk   = _first_present(obj, ["time", "times", "label_times", "labeling_time"])
        labels, lk  = _first_present(obj, ["label_values", "labels", "y"])

        if feats is None or pids is None or times is None:
            raise ValueError(
                f"{pkl_path} 里没有期望的键；已找到键：{list(obj.keys())}\n"
                f"需要 features/representations/X/data_matrix + patient_id/patient_ids/pids + time/times/label_times/labeling_time"
            )

        # 规整成 DataFrame（时间统一到分钟级 ISO）
        def _to_iso_minute(x):
            if isinstance(x, str):
                try:
                    dt = datetime.datetime.fromisoformat(x)
                except Exception:
                    dt = pd.to_datetime(x).to_pydatetime()
            else:
                dt = pd.to_datetime(x).to_pydatetime()
            return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")

        rows_df = pd.DataFrame({
            "patient_id": np.asarray(pids).astype(int),
            "time": [ _to_iso_minute(t) for t in times ],
        })
        if labels is not None and len(labels) == len(rows_df):
            rows_df["label"] = np.asarray(labels)
        # 不强制转稠密，保持原格式（ndarray 或 scipy.sparse）
        return feats, rows_df

    # B) 二元组形式: (features, rows) 或 (features, (pids, times))
    if isinstance(obj, (list, tuple)) and len(obj) == 2:
        feats, rows = obj
        if isinstance(rows, pd.DataFrame):
            rows_df = rows.copy()
        else:
            rows = np.asarray(rows)
            assert rows.shape[1] == 2, f"第二元应是两列 (patient_id, time)，实际: {rows.shape}"
            rows_df = pd.DataFrame(rows, columns=["patient_id", "time"])
        rows_df["patient_id"] = rows_df["patient_id"].astype(int)
        def _coerce(x):
            if isinstance(x, str):
                try:
                    dt = datetime.datetime.fromisoformat(x)
                except Exception:
                    dt = pd.to_datetime(x).to_pydatetime()
            else:
                dt = pd.to_datetime(x).to_pydatetime()
            return dt.replace(second=0, microsecond=0).isoformat(timespec="minutes")
        rows_df["time"] = rows_df["time"].apply(_coerce)
        return feats, rows_df

    raise ValueError(f"无法识别的 CLMBR pkl 结构：{type(obj)}（路径：{pkl_path}）")


In [12]:
# === 1) 工具函数：时间戳 & 参数快照 & 写入报告 ===
import os, json
from datetime import datetime
try:
    from zoneinfo import ZoneInfo  # py>=3.9
except Exception:
    ZoneInfo = None

def _timestamp_str():
    tz = ZoneInfo("Asia/Jakarta") if ZoneInfo else None
    return datetime.now(tz).strftime("%Y%m%d-%H%M%S%z")

def _snapshot_lr_params(clf):
    """
    从 clf（可能是 Pipeline 或 LogisticRegression 实例）提取训练参数。
    """
    lr = None
    if hasattr(clf, "named_steps") and "logisticregression" in clf.named_steps:
        lr = clf.named_steps["logisticregression"]
        scaler = type(clf.named_steps.get("maxabsscaler", None)).__name__ if "maxabsscaler" in clf.named_steps else None
    else:
        lr = clf
        scaler = None
    snap = {
        "is_pipeline": hasattr(clf, "named_steps"),
        "scaler": scaler,
        "solver": getattr(lr, "solver", None),
        "penalty": getattr(lr, "penalty", None),
        "C": getattr(lr, "C", None),
        "tol": getattr(lr, "tol", None),
        "max_iter": getattr(lr, "max_iter", None),
        "class_weight": getattr(lr, "class_weight", None),
        "random_state": getattr(lr, "random_state", None),
        "n_iter_": getattr(lr, "n_iter_", None),
    }
    if hasattr(snap["n_iter_"], "tolist"):
        snap["n_iter_"] = snap["n_iter_"].tolist()
    return snap

def _save_run_txt(summary_df, all_results, extra_params=None, out_dir="runs", fname_prefix="report"):
    os.makedirs(out_dir, exist_ok=True)
    ts = _timestamp_str()
    path = os.path.join(out_dir, f"{fname_prefix}-{ts}.txt")

    # 收集唯一的训练参数快照（若结果中已塞入 param_snapshot）
    param_snaps = [r.get("param_snapshot") for r in all_results if r.get("param_snapshot") is not None]
    uniq_snaps = []
    for p in param_snaps:
        if p and p not in uniq_snaps:
            uniq_snaps.append(p)

    with open(path, "w", encoding="utf-8") as f:
        f.write(f"===== Run Report =====\n")
        f.write(f"time: {ts}\n")
        if extra_params:
            f.write("\n--- run_config ---\n")
            f.write(json.dumps(extra_params, ensure_ascii=False, indent=2, sort_keys=True))
            f.write("\n")

        f.write("\n--- training_params (unique heads) ---\n")
        if uniq_snaps:
            for i, p in enumerate(uniq_snaps):
                f.write(f"[{i}] {json.dumps(p, ensure_ascii=False, indent=2, sort_keys=True)}\n")
        else:
            f.write("(no param_snapshot found in results)\n")

        f.write("\n--- SUMMARY (DataFrame) ---\n")
        f.write(summary_df.to_string(index=False))
        f.write("\n")

        f.write("\n--- ALL RESULTS (JSON per row) ---\n")
        for r in all_results:
            f.write(json.dumps(r, ensure_ascii=False, indent=2, sort_keys=True) + "\n")
    return path

In [13]:
# ==================== 训练 & 评估 ====================
@dataclass
class SplitData:
    X:     object                 # csr_matrix 或 ndarray
    rows:  pd.DataFrame
    idxs:  np.ndarray             # 选出来的行索引
    y:     np.ndarray             # 标签(0/1)

def slice_rows(X, idxs: np.ndarray):
    if isinstance(X, csr_matrix):
        return X[idxs]
    X = np.asarray(X)
    return X[idxs]

def evaluate_binary(y_true: np.ndarray, prob: np.ndarray, thr: float = 0.5) -> Dict[str, float]:
    out = {}
    try:
        out["auroc"] = float(roc_auc_score(y_true, prob))
    except Exception:
        out["auroc"] = float("nan")
    try:
        out["auprc"] = float(average_precision_score(y_true, prob))
    except Exception:
        out["auprc"] = float("nan")
    try:
        out["brier"] = float(brier_score_loss(y_true, prob))
    except Exception:
        out["brier"] = float("nan")
    pred = (prob >= thr).astype(int)
    out["acc@0.5"] = float(accuracy_score(y_true, pred))
    out["pos_rate"] = float(np.mean(y_true))
    return out

def fit_lr_lbfgs(X_train, y_train) -> LogisticRegression:
    # 简单稳健的逻辑回归；可以按需加 class_weight="balanced"
    model = LogisticRegression(
        solver="lbfgs",
        max_iter=2000,
        n_jobs=-1,
        verbose=0,
        class_weight=None,
    )
    model.fit(X_train, y_train)
    return model

from sklearn.pipeline import make_pipeline
from sklearn.preprocessing import MaxAbsScaler
from sklearn.linear_model import LogisticRegression
import numpy as np

def fit_lr_saga(X, y, C=1.0, tol=1e-6, max_iter=5000, balanced=False, seed=0):
    # 稀疏安全缩放 + SAGA
    class_w = "balanced" if balanced else None
    clf = make_pipeline(
        MaxAbsScaler(),
        LogisticRegression(
            solver="saga", penalty="l2", C=C, tol=tol, max_iter=max_iter,
            n_jobs=-1, verbose=0, class_weight=class_w, random_state=seed
        )
    )
    clf.fit(X, y)
    return clf

In [13]:
from scipy.sparse import csr_matrix, issparse
from sklearn.utils.sparsefuncs import inplace_column_scale

def _ensure_csr32(X):
    if not issparse(X):
        X = csr_matrix(X)
    X = X.tocsr()
    if X.dtype != np.float32:
        X = X.astype(np.float32)
    return X

def fit_lr_saga_staged(X, y, C=1.0, seed=0, max_total=2000, step=200, tol=1e-4, balanced=True, verbose=0):
    class_w = "balanced" if balanced else None
    clf = LogisticRegression(
        solver="saga", penalty="l2", C=C,
        tol=tol, max_iter=step, warm_start=True,
        n_jobs=1, verbose=verbose, class_weight=class_w,
        random_state=seed,
    )
    total = 0
    while total < max_total:
        clf.fit(X, y)
        total += step
        # 若已在本阶段内收敛则提前退出
        if hasattr(clf, "n_iter_") and np.all(clf.n_iter_ < clf.max_iter):
            break
        clf.max_iter += step
    return clf

def run_one_model(model_type: str, shots_for_k: dict):
    logger.info(f"=== [{model_type}] 开始加载特征 ===")
    if model_type == "count":
        X_tr, rows_tr, y_tr_all = load_count_split(COUNT_FILES["train"])
        X_va, rows_va, y_va_all = load_count_split(COUNT_FILES["tuning"])
        X_te, rows_te, y_te_all = load_count_split(COUNT_FILES["held"])

        # —— 一次性：转 CSR/float32 并 MaxAbs 缩放（避免每个 rep 里重复缩放）
        X_tr = _ensure_csr32(X_tr); X_va = _ensure_csr32(X_va); X_te = _ensure_csr32(X_te)
        scaler = MaxAbsScaler(copy=False)
        scaler.fit(X_tr)
        scale = scaler.scale_.astype(np.float32)
        inv = np.ones_like(scale, dtype=np.float32)
        nz = scale != 0
        inv[nz] = 1.0 / scale[nz]

        X_tr_s = X_tr.copy(); inplace_column_scale(X_tr_s, inv)
        X_va_s = X_va.copy(); inplace_column_scale(X_va_s, inv)
        X_te_s = X_te.copy(); inplace_column_scale(X_te_s, inv)
    else:
        X_tr, rows_tr = load_clmbr_split(CLMBR_FILES["train"])
        X_va, rows_va = load_clmbr_split(CLMBR_FILES["tuning"])
        X_te, rows_te = load_clmbr_split(CLMBR_FILES["held"])

    held_instances = instances_from_labeled_csv(HELDOUT["labels"], LABELING_FUNCTION)
    idx_te, y_te = _join_rows(rows_te, held_instances)
    logger.info(f"[{model_type}] held_out 对齐: {len(idx_te)}/{len(held_instances)}")

    results = []
    for rep, payload in shots_for_k.items():
        tr_samples = list(zip(payload["patient_ids_train_k"],
                              payload["label_times_train_k"],
                              payload["label_values_train_k"]))
        va_samples = list(zip(payload["patient_ids_val_k"],
                              payload["label_times_val_k"],
                              payload["label_values_val_k"]))
        idx_tr, y_tr = _join_rows(rows_tr, tr_samples)
        idx_va, y_va = _join_rows(rows_va, va_samples)

        logger.info(f"[{model_type}|rep={rep}] train 对齐: {len(idx_tr)}/{len(tr_samples)}, "
                    f"val 对齐: {len(idx_va)}/{len(va_samples)}")

        # —— 切片（count 用已缩放矩阵；clmbr 原样）
        if model_type == "count":
            Xtr = slice_rows(X_tr_s, idx_tr)
            Xva = slice_rows(X_va_s, idx_va)
            Xte = slice_rows(X_te_s, idx_te)
        else:
            Xtr = slice_rows(X_tr, idx_tr)
            Xva = slice_rows(X_va, idx_va)
            Xte = slice_rows(X_te, idx_te)

        # === 训练 ===
        if model_type == "count" or model_type == "clmbr":
            # 粗网格挑 C（更快）：减少“卡住”体感
            C_grid = [0.3, 1.0, 3.0]
            best = None
            for C in C_grid:
                clf_try = fit_lr_saga_staged(Xtr, y_tr, C=C, seed=rep, max_total=2000, step=200, tol=1e-4, balanced=True, verbose=1)
                p_va_try = clf_try.predict_proba(Xva)[:, 1]
                auroc = roc_auc_score(y_va, p_va_try)
                if best is None or auroc > best[0]:
                    best = (auroc, C, clf_try)
            logger.info(f"[count|rep={rep}] SAGA best C={best[1]} (AUROC={best[0]:.4f})")
            clf = best[2]
        else:
            clf = fit_lr_lbfgs(Xtr, y_tr)

        # === 评估 ===
        p_tr = clf.predict_proba(Xtr)[:, 1]
        p_va = clf.predict_proba(Xva)[:, 1]
        p_te = clf.predict_proba(Xte)[:, 1]
        m_tr = evaluate_binary(y_tr, p_tr)
        m_va = evaluate_binary(y_va, p_va)
        m_te = evaluate_binary(y_te, p_te)

        best_thr, _ = find_best_f1_threshold(y_va, p_va)
        f1_05_tr = f1_at_threshold(y_tr, p_tr, 0.5)
        f1_05_va = f1_at_threshold(y_va, p_va, 0.5)
        f1_05_te = f1_at_threshold(y_te, p_te, 0.5)
        f1b_tr = f1_at_threshold(y_tr, p_tr, best_thr)
        f1b_va = f1_at_threshold(y_va, p_va, best_thr)
        f1b_te = f1_at_threshold(y_te, p_te, best_thr)

        logger.success(
            f"[{model_type}|rep={rep}] "
            f"AUROC (tr/va/te) = {m_tr['auroc']:.4f} / {m_va['auroc']:.4f} / {m_te['auroc']:.4f}  | "
            f"AUPRC (tr/va/te) = {m_tr['auprc']:.4f} / {m_va['auprc']:.4f} / {m_te['auprc']:.4f}  | "
            f"F1@0.5 (tr/va/te) = {f1_05_tr['f1']:.3f} / {f1_05_va['f1']:.3f} / {f1_05_te['f1']:.3f}"
        )
        logger.info(
            f"[{model_type}|rep={rep}] F1@val-best({best_thr:.3f}) "
            f"(tr/va/te) = {f1b_tr['f1']:.3f} / {f1b_va['f1']:.3f} / {f1b_te['f1']:.3f}  | "
            f"P/R@test = {f1b_te['precision']:.3f}/{f1b_te['recall']:.3f}"
        )

        param_snapshot = _snapshot_lr_params(clf)
        results.append({
            "model": model_type,
            "rep": rep,
            "metrics_train": m_tr,
            "metrics_val": m_va,
            "metrics_test": m_te,
            "thresholds": {"fixed_0.5": 0.5, "best_on_val": best_thr},
            "f1_at_0.5": {
                "train": {"f1": f1_05_tr["f1"], "precision": f1_05_tr["precision"], "recall": f1_05_tr["recall"]},
                "val":   {"f1": f1_05_va["f1"], "precision": f1_05_va["precision"], "recall": f1_05_va["recall"]},
                "test":  {"f1": f1_05_te["f1"], "precision": f1_05_te["precision"], "recall": f1_05_te["recall"]},
            },
            "f1_at_best": {
                "train": {"f1": f1b_tr["f1"], "precision": f1b_tr["precision"], "recall": f1b_tr["recall"]},
                "val":   {"f1": f1b_va["f1"], "precision": f1b_va["precision"], "recall": f1b_va["recall"]},
                "test":  {"f1": f1b_te["f1"], "precision": f1b_te["precision"], "recall": f1b_te["recall"]},
            },
            "param_snapshot": param_snapshot,
            "data_stats": {
                "n_train": int(len(y_tr)), "pos_train": int(y_tr.sum()),
                "n_val":   int(len(y_va)), "pos_val":  int(y_va.sum()),
                "n_test":  int(len(y_te)), "pos_test": int(y_te.sum()),
            },
        })
    return results


In [15]:
# ==================== 主流程：按 K & 模型 循环 ====================
warnings.filterwarnings("ignore", category=UserWarning)

assert os.path.exists(SHOTS_JSON), f"找不到 shots JSON: {SHOTS_JSON}"
shots = load_shots(SHOTS_JSON, LABELING_FUNCTION, K_VALUES)

In [16]:
import pandas as pd

def eval_one_model(model_name: str, save_txt: bool = True, out_dir: str = "runs"):
    all_results = []
    for k, reps in shots.items():
        logger.info(f"******** K={k}（{'ALL' if k==-1 else 'FEW'}） | model={model_name} ********")
        res = run_one_model(model_name, reps)
        for r in res:
            r["k"] = k
            r["model"] = model_name
        all_results.extend(res)

    # 汇总成 DataFrame
    rows = []
    for r in all_results:
        rows.append({
            "k": r["k"],
            "model": r["model"],
            "rep": r["rep"],
            "val_auroc": r["metrics_val"]["auroc"],
            "val_auprc": r["metrics_val"]["auprc"],
            "val_brier": r["metrics_val"]["brier"],
            "test_auroc": r["metrics_test"]["auroc"],
            "test_auprc": r["metrics_test"]["auprc"],
            "test_brier": r["metrics_test"]["brier"],
            "test_acc@0.5": r["metrics_test"]["acc@0.5"],
            "test_pos_rate": r["metrics_test"]["pos_rate"],
            "val_f1@0.5":   r["f1_at_0.5"]["val"]["f1"],
            "test_f1@0.5":  r["f1_at_0.5"]["test"]["f1"],
            "val_f1@best":  r["f1_at_best"]["val"]["f1"],
            "test_f1@best": r["f1_at_best"]["test"]["f1"],
            "best_thr":     r["thresholds"]["best_on_val"],
        })
    summary = pd.DataFrame(rows).sort_values(by=["k","model","rep"]).reset_index(drop=True)
    print(f"\n===== Summary for model: {model_name} =====")
    print(summary)

    if save_txt:
        # 可把你的网格、随机种子等外部配置也放进 extra_params 里，便于复现
        extra = {
            "model": model_name,
            "k_values": list(shots.keys()),
            # 如果你有 C_grid / tol / max_iter 等全局设置，也可放进来
            # "C_grid": C_grid,
        }
        out_fp = _save_run_txt(summary, all_results, extra_params=extra, out_dir=out_dir, fname_prefix=f"{model_name}")
        print(f"[Saved] TXT report -> {out_fp}")

    return summary, all_results


## Count Model

In [19]:
# 👇 分别评估两个模型（不再 for 循环 MODELS）
summary_m0 = eval_one_model(MODELS[0])

2025-09-06 21:38:27.332 | INFO     | __main__:eval_one_model:44 - ******** K=-1（ALL） | model=count ********
2025-09-06 21:38:27.334 | INFO     | __main__:run_one_model:36 - === [count] 开始加载特征 ===
2025-09-06 21:38:29.905 | INFO     | __main__:run_one_model:61 - [count] held_out 对齐: 5815/5815
2025-09-06 21:38:29.975 | INFO     | __main__:run_one_model:74 - [count|rep=0] train 对齐: 46113/46113, val 对齐: 5602/5602


Epoch 1, change: 1.00000000
Epoch 2, change: 0.37881136
Epoch 3, change: 0.21957697
Epoch 4, change: 0.15446047
Epoch 5, change: 0.12051927
Epoch 6, change: 0.10081327
Epoch 7, change: 0.08206557
Epoch 8, change: 0.07265287
Epoch 9, change: 0.06199510
Epoch 10, change: 0.05501575
Epoch 11, change: 0.04995129
Epoch 12, change: 0.04677152
Epoch 13, change: 0.04011704
Epoch 14, change: 0.03753484
Epoch 15, change: 0.03661080
Epoch 16, change: 0.03242249
Epoch 17, change: 0.02852731
Epoch 18, change: 0.03048830
Epoch 19, change: 0.02643944
Epoch 20, change: 0.02406992
Epoch 21, change: 0.02300341
Epoch 22, change: 0.02226586
Epoch 23, change: 0.02162304
Epoch 24, change: 0.02146771
Epoch 25, change: 0.01953538
Epoch 26, change: 0.01919692
Epoch 27, change: 0.01757304
Epoch 28, change: 0.01760664
Epoch 29, change: 0.01718418
Epoch 30, change: 0.01681685
Epoch 31, change: 0.01445527
Epoch 32, change: 0.01422978
Epoch 33, change: 0.01372366
Epoch 34, change: 0.01345838
Epoch 35, change: 0.013

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   41.6s finished


h 141, change: 0.00110061
Epoch 142, change: 0.00107988
Epoch 143, change: 0.00106752
Epoch 144, change: 0.00104579
Epoch 145, change: 0.00103561
Epoch 146, change: 0.00102097
Epoch 147, change: 0.00101054
Epoch 148, change: 0.00098354
Epoch 149, change: 0.00097463
Epoch 150, change: 0.00096250
Epoch 151, change: 0.00095119
Epoch 152, change: 0.00093770
Epoch 153, change: 0.00092269
Epoch 154, change: 0.00091128
Epoch 155, change: 0.00089667
Epoch 156, change: 0.00088475
Epoch 157, change: 0.00085263
Epoch 158, change: 0.00084623
Epoch 159, change: 0.00083358
Epoch 160, change: 0.00082103
Epoch 161, change: 0.00080961
Epoch 162, change: 0.00080110
Epoch 163, change: 0.00079352
Epoch 164, change: 0.00078030
Epoch 165, change: 0.00077167
Epoch 166, change: 0.00076280
Epoch 167, change: 0.00074709
Epoch 168, change: 0.00073398
Epoch 169, change: 0.00072653
Epoch 170, change: 0.00071366
Epoch 171, change: 0.00070842
Epoch 172, change: 0.00070045
Epoch 173, change: 0.00069147
Epoch 174, cha

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:   23.1s finished


...

 change: 0.00022214
Epoch 478, change: 0.00022033
Epoch 479, change: 0.00022001
Epoch 480, change: 0.00022127
Epoch 481, change: 0.00022071
Epoch 482, change: 0.00021908
Epoch 483, change: 0.00022006
Epoch 484, change: 0.00022064
Epoch 485, change: 0.00022190
Epoch 486, change: 0.00022067
Epoch 487, change: 0.00021943
Epoch 488, change: 0.00022149
Epoch 489, change: 0.00022048
Epoch 490, change: 0.00021941
Epoch 491, change: 0.00021931
Epoch 492, change: 0.00021808
Epoch 493, change: 0.00021803
Epoch 494, change: 0.00021805
Epoch 495, change: 0.00021942
Epoch 496, change: 0.00021910
Epoch 497, change: 0.00021758
Epoch 498, change: 0.00021685
Epoch 499, change: 0.00021732
Epoch 500, change: 0.00021733
Epoch 501, change: 0.00021724
Epoch 502, change: 0.00021787
Epoch 503, change: 0.00021794
Epoch 504, change: 0.00021914
Epoch 505, change: 0.00021667
Epoch 506, change: 0.00021679
Epoch 507, change: 0.00021975
Epoch 508, change: 0.00021529
Epoch 509, change: 0.00021729
Epoch 510, change: 0

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:  2.8min finished


h 700, change: 0.00012737
Epoch 701, change: 0.00012664
Epoch 702, change: 0.00012791
Epoch 703, change: 0.00012596
Epoch 704, change: 0.00012523
Epoch 705, change: 0.00012753
Epoch 706, change: 0.00012854
Epoch 707, change: 0.00012812
Epoch 708, change: 0.00012648
Epoch 709, change: 0.00012631
Epoch 710, change: 0.00012717
Epoch 711, change: 0.00012640
Epoch 712, change: 0.00012782
Epoch 713, change: 0.00012602
Epoch 714, change: 0.00012658
Epoch 715, change: 0.00012651
Epoch 716, change: 0.00012692
Epoch 717, change: 0.00012660
Epoch 718, change: 0.00012746
Epoch 719, change: 0.00012556
Epoch 720, change: 0.00012698
Epoch 721, change: 0.00012672
Epoch 722, change: 0.00012620
Epoch 723, change: 0.00012731
Epoch 724, change: 0.00012531
Epoch 725, change: 0.00012832
Epoch 726, change: 0.00012626
Epoch 727, change: 0.00012656
Epoch 728, change: 0.00012635
Epoch 729, change: 0.00012603
Epoch 730, change: 0.00012587
Epoch 731, change: 0.00012657
Epoch 732, change: 0.00012728
Epoch 733, cha

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:  1.9min finished
2025-09-06 21:51:14.756 | INFO     | __main__:run_one_model:98 - [count|rep=0] SAGA best C=0.3 (AUROC=0.8123)
2025-09-06 21:51:14.865 | SUCCESS  | __main__:run_one_model:119 - [count|rep=0] AUROC (tr/va/te) = 0.9615 / 0.8123 / 0.8294  | AUPRC (tr/va/te) = 0.6582 / 0.3023 / 0.2840  | F1@0.5 (tr/va/te) = 0.535 / 0.350 / 0.350
2025-09-06 21:51:14.866 | INFO     | __main__:run_one_model:125 - [count|rep=0] F1@val-best(0.707) (tr/va/te) = 0.650 / 0.393 / 0.357  | P/R@test = 0.336/0.382


convergence after 551 epochs took 113 seconds

===== Summary for model: count =====
   k  model  rep  val_auroc  val_auprc  val_brier  test_auroc  test_auprc  \
0 -1  count    0   0.812326   0.302316   0.120482     0.82941    0.283964   

   test_brier  test_acc@0.5  test_pos_rate  val_f1@0.5  test_f1@0.5  \
0    0.117916      0.847635       0.064832    0.350037      0.35044   

   val_f1@best  test_f1@best  best_thr  
0     0.392547       0.35732  0.706949  
[Saved] TXT report -> runs/count-20250906-205114+0700.txt


## CLMBR Model

In [ ]:
summary_m1 = eval_one_model(MODELS[1])

2025-09-06 22:02:53.323 | INFO     | __main__:eval_one_model:44 - ******** K=-1（ALL） | model=clmbr ********
2025-09-06 22:02:53.326 | INFO     | __main__:run_one_model:36 - === [clmbr] 开始加载特征 ===
2025-09-06 22:02:55.865 | INFO     | __main__:run_one_model:61 - [clmbr] held_out 对齐: 5815/5815
2025-09-06 22:02:55.940 | INFO     | __main__:run_one_model:74 - [clmbr|rep=0] train 对齐: 46113/46113, val 对齐: 5602/5602


741
Epoch 450, change: 0.00010371
Epoch 451, change: 0.00010508
Epoch 452, change: 0.00010508
Epoch 453, change: 0.00010295
Epoch 454, change: 0.00010462
Epoch 455, change: 0.00010629
Epoch 456, change: 0.00010293
Epoch 457, change: 0.00010420
Epoch 458, change: 0.00010543
Epoch 459, change: 0.00010384
Epoch 460, change: 0.00010477
Epoch 461, change: 0.00010654
Epoch 462, change: 0.00010436
Epoch 463, change: 0.00010534
Epoch 464, change: 0.00010361
Epoch 465, change: 0.00010409
Epoch 466, change: 0.00010325
Epoch 467, change: 0.00010428
Epoch 468, change: 0.00010496
Epoch 469, change: 0.00010569
Epoch 470, change: 0.00010332
Epoch 471, change: 0.00010322
Epoch 472, change: 0.00010272
Epoch 473, change: 0.00010369
Epoch 474, change: 0.00010502
Epoch 475, change: 0.00010540
Epoch 476, change: 0.00010377
Epoch 477, change: 0.00010371
Epoch 478, change: 0.00010518
Epoch 479, change: 0.00010572
Epoch 480, change: 0.00010379
Epoch 481, change: 0.00010260
Epoch 482, change: 0.00010274
Epoch 

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:  2.3min finished


e: 0.36057378
Epoch 177, change: 0.38707248
Epoch 178, change: 0.52278286
Epoch 179, change: 0.48048588
Epoch 180, change: 0.48185559
Epoch 181, change: 0.48150166
Epoch 182, change: 0.43584575
Epoch 183, change: 0.34641272
Epoch 184, change: 0.37125299
Epoch 185, change: 0.42713541
Epoch 186, change: 0.47469005
Epoch 187, change: 0.42083662
Epoch 188, change: 0.43431168
Epoch 189, change: 0.52910376
Epoch 190, change: 0.38444278
Epoch 191, change: 0.54748313
Epoch 192, change: 0.44432133
Epoch 193, change: 0.41024977
Epoch 194, change: 0.38092669
Epoch 195, change: 0.45912461
Epoch 196, change: 0.43786551
Epoch 197, change: 0.46608821
Epoch 198, change: 0.43151906
Epoch 199, change: 0.44067395
Epoch 200, change: 0.43645681
Epoch 1, change: 1.00000000
Epoch 2, change: 0.55232602
Epoch 3, change: 0.44499531
Epoch 4, change: 0.49217122
Epoch 5, change: 0.43104385
Epoch 6, change: 0.44956238
Epoch 7, change: 0.46271329
Epoch 8, change: 0.38308751
Epoch 9, change: 0.38166755
Epoch 10, chan

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:  4.5min finished


...

Epoch 1149, change: 0.40281034
Epoch 1150, change: 0.41584882
Epoch 1151, change: 0.57263085
Epoch 1152, change: 0.45256219
Epoch 1153, change: 0.52148102
Epoch 1154, change: 0.42983430
Epoch 1155, change: 0.52963123
Epoch 1156, change: 0.43050288
Epoch 1157, change: 0.40759567
Epoch 1158, change: 0.40434436
Epoch 1159, change: 0.42550183
Epoch 1160, change: 0.39966361
Epoch 1161, change: 0.45057718
Epoch 1162, change: 0.40644961
Epoch 1163, change: 0.42037287
Epoch 1164, change: 0.44952664
Epoch 1165, change: 0.49944302
Epoch 1166, change: 0.40852877
Epoch 1167, change: 0.35666843
Epoch 1168, change: 0.38707685
Epoch 1169, change: 0.43560886
Epoch 1170, change: 0.44029829
Epoch 1171, change: 0.44435390
Epoch 1172, change: 0.47241793
Epoch 1173, change: 0.44301360
Epoch 1174, change: 0.53848279
Epoch 1175, change: 0.53975388
Epoch 1176, change: 0.44104738
Epoch 1177, change: 0.50306725
Epoch 1178, change: 0.48879169
Epoch 1179, change: 0.46196439
Epoch 1180, change: 0.40416994
Epoch 11

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed: 15.8min finished


Epoch 1306, change: 0.43237004
Epoch 1307, change: 0.39698489
Epoch 1308, change: 0.43321140
Epoch 1309, change: 0.42296461
Epoch 1310, change: 0.55577231
Epoch 1311, change: 0.42956482
Epoch 1312, change: 0.43172910
Epoch 1313, change: 0.43782959
Epoch 1314, change: 0.45760225
Epoch 1315, change: 0.41001030
Epoch 1316, change: 0.36793815
Epoch 1317, change: 0.41389524
Epoch 1318, change: 0.61244805
Epoch 1319, change: 0.38814442
Epoch 1320, change: 0.41305037
Epoch 1321, change: 0.39035615
Epoch 1322, change: 0.40766073
Epoch 1323, change: 0.47991458
Epoch 1324, change: 0.48330203
Epoch 1325, change: 0.43969597
Epoch 1326, change: 0.42499264
Epoch 1327, change: 0.46306658
Epoch 1328, change: 0.49974811
Epoch 1329, change: 0.55428590
Epoch 1330, change: 0.41227968
Epoch 1331, change: 0.48712020
Epoch 1332, change: 0.46038802
Epoch 1333, change: 0.42855831
Epoch 1334, change: 0.59902644
Epoch 1335, change: 0.45838880
Epoch 1336, change: 0.42075586
Epoch 1337, change: 0.47743004
Epoch 13

[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed: 18.0min finished


27, change: 0.39802342
Epoch 1528, change: 0.33229540
Epoch 1529, change: 0.39707891
Epoch 1530, change: 0.54991277
Epoch 1531, change: 0.37366799
Epoch 1532, change: 0.44768481
Epoch 1533, change: 0.37291950
Epoch 1534, change: 0.47863137
Epoch 1535, change: 0.38945588
Epoch 1536, change: 0.43604440
Epoch 1537, change: 0.44283016
Epoch 1538, change: 0.55398671
Epoch 1539, change: 0.45074341
Epoch 1540, change: 0.50874322
Epoch 1541, change: 0.37818164
Epoch 1542, change: 0.43709521
Epoch 1543, change: 0.43094090
Epoch 1544, change: 0.40617074
Epoch 1545, change: 0.41953674
Epoch 1546, change: 0.56790382
Epoch 1547, change: 0.51966226
Epoch 1548, change: 0.40669602
Epoch 1549, change: 0.49731201
Epoch 1550, change: 0.44333826
Epoch 1551, change: 0.38458820
Epoch 1552, change: 0.46710361
Epoch 1553, change: 0.45366262
Epoch 1554, change: 0.40151253
Epoch 1555, change: 0.47641408
Epoch 1556, change: 0.43885114
Epoch 1557, change: 0.47479194
Epoch 1558, change: 0.45077222
Epoch 1559, chan

In [51]:


all_results = []
for k, reps in shots.items():
    logger.info(f"******** K={k}（{'ALL' if k==-1 else 'FEW'}）********")
    for m in MODELS:
        res = run_one_model(m, reps)
        # 附上 k 信息
        for r in res:
            r["k"] = k
        all_results.extend(res)

# 汇总表
rows = []
for r in all_results:
    rows.append({
        "k": r["k"],
        "model": r["model"],
        "rep": r["rep"],
        "val_auroc": r["metrics_val"]["auroc"],
        "val_auprc": r["metrics_val"]["auprc"],
        "val_brier": r["metrics_val"]["brier"],
        "test_auroc": r["metrics_test"]["auroc"],
        "test_auprc": r["metrics_test"]["auprc"],
        "test_brier": r["metrics_test"]["brier"],
        "test_acc@0.5": r["metrics_test"]["acc@0.5"],
        "test_pos_rate": r["metrics_test"]["pos_rate"],
    })
summary = pd.DataFrame(rows).sort_values(by=["k","model","rep"]).reset_index(drop=True)
summary

2025-09-05 06:00:16.286 | INFO     | __main__:<module>:9 - ******** K=-1（ALL）********
2025-09-05 06:00:16.288 | INFO     | __main__:run_one_model:167 - === [count] 开始加载特征 ===
2025-09-05 06:00:17.994 | INFO     | __main__:run_one_model:181 - [count] held_out 对齐: 5815/5815
2025-09-05 06:00:18.060 | INFO     | __main__:run_one_model:194 - [count|rep=0] train 对齐: 46113/46113, val 对齐: 5602/5602
2025-09-05 06:00:18.062 | INFO     | __main__:run_one_model:212 - [sanity] train pos=3202/46113, val pos=372/5602, test pos=377/5815
/root/miniconda3/envs/ehr-env/lib/python3.10/site-packages/sklearn/linear_model/_logistic.py:458: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#l

ValueError: The truth value of an array with more than one element is ambiguous. Use a.any() or a.all()

In [9]:
import pickle, numpy as np, pandas as pd

PKL = "/root/autodl-tmp/femr/train/femr_features/count_features.pkl"  # 改成你的路径

with open(PKL, "rb") as f:
    obj = pickle.load(f)

print("TOP:", type(obj))
if isinstance(obj, dict):
    print("  keys:", list(obj.keys())[:50])
    for k,v in obj.items():
        if isinstance(v, (np.ndarray, pd.DataFrame, list, tuple)):
            try:
                shape = v.shape if hasattr(v, "shape") else len(v)
            except Exception:
                shape = "?"
            print(f"   - {k}: {type(v)}, shape/len={shape}")
        else:
            print(f"   - {k}: {type(v)}")

elif isinstance(obj, (list, tuple)):
    print("  len =", len(obj))
    for i,v in enumerate(obj[:10]):
        if isinstance(v, (np.ndarray, pd.DataFrame, list, tuple)):
            try:
                shape = v.shape if hasattr(v, "shape") else len(v)
            except Exception:
                shape = "?"
            print(f"   [{i}] {type(v)}, shape/len={shape}")
        else:
            print(f"   [{i}] {type(v)}")

else:
    print("  (unknown top-level)")


TOP: <class 'tuple'>
  len = 4
   [0] <class 'scipy.sparse._csr.csr_matrix'>
   [1] <class 'numpy.ndarray'>, shape/len=(46113,)
   [2] <class 'numpy.ndarray'>, shape/len=(46113,)
   [3] <class 'numpy.ndarray'>, shape/len=(46113,)


In [13]:
import pickle, numpy as np, pandas as pd
from scipy.sparse import issparse, csr_matrix

def probe_count_pkl(path, max_preview=5, show_row_example=0):
    print(f"\n=== {path} ===")
    with open(path, "rb") as f:
        obj = pickle.load(f)

    print("TOP:", type(obj))

    X = pids = times = y = rows_df = None

    if isinstance(obj, dict):
        print("  keys:", list(obj.keys()))
        X = obj.get("X") or obj.get("feature_matrix") or obj.get("features") or obj.get("matrix")
        rows_df = obj.get("rows")
        pids = obj.get("patient_ids") or obj.get("pids")
        times = obj.get("label_times") or obj.get("times") or obj.get("time")
        y = obj.get("label_values")

    elif isinstance(obj, (list, tuple)):
        print("  len:", len(obj))
        for i, v in enumerate(obj[:6]):
            t = type(v)
            shape = getattr(v, "shape", None)
            if shape is None:
                try:
                    shape = len(v)
                except Exception:
                    shape = "?"
            print(f"   [{i}] {t}{' shape='+str(shape) if shape!='?' else ''}")

        # 常见： (X, patient_ids, label_times[, y]) 或 (X, rows_df[, feature_names])
        X = obj[0] if len(obj) >= 1 else None
        if len(obj) >= 2 and isinstance(obj[1], pd.DataFrame):
            rows_df = obj[1]
            print("  rows_df columns:", rows_df.columns.tolist())
        else:
            pids  = obj[1] if len(obj) >= 2 else None
            times = obj[2] if len(obj) >= 3 else None
            y     = obj[3] if len(obj) >= 4 else None

    # --- 打印各部分摘要 ---
    if X is not None:
        if issparse(X):
            print(f"X: sparse CSR {X.shape}, nnz={X.nnz}")
        else:
            print(f"X: {type(X)}, shape={np.shape(X)}")

    if rows_df is not None:
        df = rows_df.rename(columns={"pid":"patient_id", "label_time":"time", "timestamp":"time"})
        ok_cols = {"patient_id","time"}.issubset(df.columns)
        print(f"rows_df: {rows_df.shape} ; has pid/time cols? {ok_cols}")
        print(df.head(max_preview))
    else:
        if pids is not None:
            pids = np.asarray(pids)
            print(f"patient_ids: {type(pids)}, len={len(pids)}, preview={pids[:max_preview].tolist()}")
        if times is not None:
            times = np.asarray(times)
            print(f"label_times: {type(times)}, len={len(times)}, preview={times[:max_preview].tolist()}")

    if y is not None:
        y_arr = np.asarray(y)
        vals, cnts = np.unique(y_arr, return_counts=True)
        print(f"y: dtype={y_arr.dtype}, len={len(y_arr)}, unique={dict(zip(vals.tolist(), cnts.tolist()))}, preview={y_arr[:max_preview].tolist()}")

    # 可选：展示某一行的非零特征（方便 sanity check）
    if issparse(X) and X.shape[0] > show_row_example:
        r = X[show_row_example]
        print(f"row {show_row_example}: nnz={r.nnz}, first10 idx={r.indices[:10].tolist()}, vals={r.data[:10].tolist()}")

# 改成你的三份路径
probe_count_pkl("/root/autodl-tmp/femr/train/femr_features/count_features.pkl")
probe_count_pkl("/root/autodl-tmp/femr/tuning/femr_features/count_features.pkl")
probe_count_pkl("/root/autodl-tmp/femr/held_out/femr_features/count_features.pkl")


=== /root/autodl-tmp/femr/train/femr_features/count_features.pkl ===
TOP: <class 'tuple'>
  len: 4
   [0] <class 'scipy.sparse._csr.csr_matrix'> shape=(46113, 51281)
   [1] <class 'numpy.ndarray'> shape=(46113,)
   [2] <class 'numpy.ndarray'> shape=(46113,)
   [3] <class 'numpy.ndarray'> shape=(46113,)
X: sparse CSR (46113, 51281), nnz=10045712
patient_ids: <class 'numpy.ndarray'>, len=46113, preview=[10001217, 10001725, 10001884, 10002013, 10002348]
label_times: <class 'numpy.ndarray'>, len=46113, preview=[False, False, False, False, False]
y: dtype=datetime64[us], len=46113, unique={datetime.datetime(2110, 1, 12, 10, 16): 1, datetime.datetime(2110, 1, 13, 0, 54): 1, datetime.datetime(2110, 1, 14, 9, 9): 1, datetime.datetime(2110, 1, 15, 7, 22): 1, datetime.datetime(2110, 1, 18, 0, 28): 1, datetime.datetime(2110, 1, 19, 14, 46): 1, datetime.datetime(2110, 1, 19, 17, 47): 1, datetime.datetime(2110, 1, 21, 14, 1): 1, datetime.datetime(2110, 1, 21, 21, 6): 1, datetime.datetime(2110, 1, 